In [257]:
import pandas as pd
import numpy as np
import itertools
from datetime import datetime,timedelta,date
from collections import defaultdict

import colorlover as cl
import random
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly
import plotly.graph_objs as go
from plotly import tools

import matplotlib.pyplot as plt
%matplotlib inline
init_notebook_mode(connected=True)

In [282]:
#df = pd.read_csv('../features/clear_data/rm_features.csv',';',infer_datetime_format=True,index_col=['time','host','consumer_group'],parse_dates=['time'])
#df = pd.read_csv('../features/clear_data/rm_features.csv',';',infer_datetime_format=True,index_col=['time'],parse_dates=['time'])
df = pd.read_csv('../features/clear_data/rm_features.csv',';',infer_datetime_format=True,parse_dates=['time'])

In [283]:
host_cons=[(host,group) for host,group in df.drop_duplicates(['host','consumer_group'])[['host','consumer_group']].values]


In [170]:
#print(*df.columns)
#columns=['time', 'host', 'consumer_group', 'cpu', 'dbtime', 'iowait', 'oth_wait',
#       'pga', 'pxenq', 'pxqry', 'pxqtime', 'pxrel', 'read', 'reqs', 'write',
#       'yields', 'sys_actsess_avg', 'sys_actsess_max', 'sys_cpu', 'sys_dbtime',
#       'sys_iowait', 'sys_oswait', 'sys_pga', 'sys_pxqct', 'sys_pxruns',
#       'sys_pxsrvt', 'sys_read', 'sys_redo', 'sys_rmwait', 'sys_syspct',
#       'sys_ucalls', 'sys_write']

#columns=['time', 'host', 'consumer_group', 'cpu', 'iowait', 'oth_wait', 'pxqtime','reqs', 'yields']


#df=df.drop(columns=['max_utilization_limit', 'mgmt_p1', 'parallel_degree_limit_p1', 'parallel_target_percentage'])

In [284]:
X_train=pd.DataFrame()
X_pred=pd.DataFrame()
for (host,consumer_group) in host_cons:
    sample=df[(df.host==host)&(df.consumer_group==consumer_group)]
    X_train=pd.concat([X_train,sample.head(int(len(sample)*0.97))],sort=False)
    X_pred=pd.concat([X_pred,sample[~sample.index.isin(X_train.index)]],sort=False)
#X_train=X_train.set_index(['time','host','consumer_group'])
#X_pred=X_pred.set_index(['time','host','consumer_group'])

In [ ]:
# Разбить временной ряд на периоды с некоторым окном и свернуть каждый период с помощью PCA

#ts_period=1 # количество дней 
#n_length=24 # количество часов


#def window_stack(a, window=ts_period*n_length):
    # разбиваем данные на окна длиной ts_period
#    X=np.array([a[i:window+i] for i in range(int(len(a) - window))])
#    return X


#from sklearn.decomposition import PCA
#model_PCA = PCA(n_components=1)

#for (host,consumer_group) in host_cons:
#    samples=window_stack(df[(df.host==host)&(df.consumer_group==consumer_group)].set_index(['host','consumer_group']).values)
    #model_PCA.fit_transform(df)
#    for sample in samples:
        

In [285]:
outliers_fraction = 0.0001
def predict(model,X_train,X_pred=None,mode=0):
    model_predict=pd.DataFrame()
    for (host,consumer_group) in host_cons:
        sample_train=X_train[(X_train.host==host)&(X_train.consumer_group==consumer_group)].set_index(['time','host','consumer_group'])
        
        if mode==0:
            sample_pred=X_pred[(X_pred.host==host)&(X_pred.consumer_group==consumer_group)].set_index(['time','host','consumer_group'])
            predict=model.fit(sample_train).predict(sample_pred)
        else:
            predict=model.fit_predict(sample_train)
            
        model_predict=pd.concat([model_predict,pd.DataFrame(predict,columns=['is_anomaly'])],sort=False)
    return model_predict.reset_index(drop=True)
        


In [ ]:
#outliers_fraction = 0.005
#def predict(model,X_train,X_pred):
#    return pd.DataFrame(model.fit(X_train).predict(X_pred),columns=['is_anomaly'])
        

## ML models

In [310]:
from sklearn.ensemble import IsolationForest

rns = np.random.RandomState(42)

#model_IF = IsolationForest(random_state=rns,contamination=outliers_fraction,n_estimators =1000)
model_IF = IsolationForest(random_state=rns,contamination=0.005,n_estimators =1000,bootstrap =True)

#anomaly_IF = predict(model_IF,X_train,X_pred)
anomaly_IF = predict(model_IF,df,df)


In [197]:
#from sklearn.neighbors import LocalOutlierFactor

#model_LOF = LocalOutlierFactor(n_neighbors=35, contamination=outliers_fraction)
#anomaly_LOF = predict(model_LOF,df,mode=1)

#from sklearn import svm

#model_SVM = svm.OneClassSVM(random_state=rns, nu=outliers_fraction, kernel="rbf", gamma=0.005)
#anomaly_SVM = predict(model_SVM,X_train,X_pred)
#anomaly_SVM = predict(model_SVM,df,df)

#from sklearn.covariance import EllipticEnvelope

#model_EE = EllipticEnvelope(contamination=outliers_fraction)
#anomaly_EE = predict(model_EE,X_train,X_pred)
#anomaly_EE = predict(model_EE,df,df)

#from sklearn.cluster import DBSCAN

#model_DBSCAN = DBSCAN(eps=4, min_samples=20)
#anomaly_DBSCAN = predict(model_DBSCAN,df,mode=1)

#anomaly_DBSCAN[anomaly_DBSCAN.is_anomaly==-1]

#from sklearn.decomposition import PCA

#model_PCA = PCA(n_components=15, svd_solver='full')
#model_PCA.fit_transform(df)

#w_components_ = np.ones([model_PCA.n_components_, ])
#selected_components_ = model_PCA.components_[-1 * model_PCA.n_selected_components_:, :]
#selected_w_components_ = w_components_[-1 * model_PCA.n_selected_components_:]

#tmp=anomaly_IF[anomaly_IF.is_anomaly==-1]\
#    .join(anomaly_SVM[anomaly_SVM.is_anomaly==-1],rsuffix ='_SVM',how='outer')\
#    .join(anomaly_EE[anomaly_EE.is_anomaly==-1],rsuffix ='_EE',how='outer')\
#    .join(anomaly_LOF[anomaly_LOF.is_anomaly==-1],rsuffix ='_LOF',how='outer')\
#    .join(anomaly_DBSCAN[anomaly_DBSCAN.is_anomaly==-1],rsuffix ='_DBSCAN',how='outer')
#tmp=tmp[tmp.sum(axis=1)<-1]
#df_predict=df.reset_index()[['time','host','consumer_group']].join(tmp,how='right')
#df_predict

In [311]:
df_predict=df.reset_index()[['time','host','consumer_group']].join(anomaly_IF[anomaly_IF.is_anomaly==-1],how='right')
df_predict[df_predict.consumer_group=='sandbox_group']

time  host consumer_group  is_anomaly
10062 2018-12-03 06:00:00     3  sandbox_group          -1
10137 2018-12-06 09:00:00     3  sandbox_group          -1
10140 2018-12-06 12:00:00     3  sandbox_group          -1
10161 2018-12-07 09:00:00     3  sandbox_group          -1
10234 2018-12-10 10:00:00     3  sandbox_group          -1
13668 2018-11-27 12:00:00     4  sandbox_group          -1
13861 2018-12-05 13:00:00     4  sandbox_group          -1
13881 2018-12-06 09:00:00     4  sandbox_group          -1
13883 2018-12-06 11:00:00     4  sandbox_group          -1
13884 2018-12-06 12:00:00     4  sandbox_group          -1

In [317]:
df_predict[df_predict.host==3].iloc[0].time+timedelta(hours=1)

Timestamp('2018-11-03 04:00:00')

## Autoencoders

In [ ]:
from keras.layers import Input, Dense
from keras.models import Model
from keras import regularizers
from keras.callbacks import TensorBoard


dim=X_train.set_index(['time','host','consumer_group']).shape[1]

X_input = Input(shape=(dim,))
encoded = Dense(64, activation='relu', activity_regularizer=regularizers.l1(10e-5))(X_input)
encoded = Dense(32, activation='relu')(encoded)
encoded = Dense(16, activation='relu')(encoded)
decoded = Dense(32, activation='relu')(encoded)
decoded = Dense(64, activation='relu')(decoded)
decoded = Dense(dim, activation='sigmoid')(decoded)

autoencoder = Model(X_input, decoded)

def autoencoder_fit_predict(model,X_train,X_pred):
    model.compile(optimizer='adam', loss='mse')

    model.fit(X_train, X_train,
                    epochs=20,
                    batch_size=64,
                    shuffle=True,
                    validation_data=(X_pred, X_pred))
    return model.predict(X_pred)

model_predict=pd.DataFrame()
for (host,consumer_group) in host_cons:
    sample_train=X_train[(X_train.host==host)&(X_train.consumer_group==consumer_group)].set_index(['time','host','consumer_group'])
    sample_pred=X_pred[(X_pred.host==host)&(X_pred.consumer_group==consumer_group)].set_index(['time','host','consumer_group'])
    
    sample_decoded=pd.DataFrame(autoencoder_fit_predict(autoencoder,sample_train,sample_pred),columns=sample_pred.columns)
    autoencoder_predict=pd.concat([sample_pred.reset_index()[['time','host','consumer_group']],sample_decoded],axis=1,sort=False)

    model_predict=pd.concat([model_predict,autoencoder_predict],sort=False)


In [ ]:
model_predict

In [ ]:
mse = np.mean(np.power(X_pred.drop(columns=['time','host','consumer_group']).values - model_predict.drop(columns=['time','host','consumer_group']).values, 2), axis=1)


In [ ]:
mse

In [ ]:
plt.plot(mse.loc[(3,'adw_unload_group')][['time']], mse.loc[(1,'adw_unload_group')][['mse']], '*')
plt.xticks(rotation='vertical')

## Visualization 

In [321]:
def show_forecast(X,metrics,consumer_group,anomaly=None):
# функция для визуализации построенного прогноза

    colors=[color for color in cl.flipper()['seq']['9'].values()]
    data_host=defaultdict(list)

    hosts=X.host.unique()
    for i,host in enumerate(hosts):
        fact_data=[]
        if i==0: 
            ButtonVisible=True
        else: 
            ButtonVisible=False

        
            

#        anomaly_data = [go.Scatter(
#
#            legendgroup='host '+str(host),   
#            x=anomaly[(host,group)][i],
#            y=[y_real[(host,group)].max()]*2,
#            fill='tozeroy',
#            fillcolor='rgba(190,127,188,0.5)',
#            line=dict(width=0),
#            mode= 'none',
#            showlegend=False,
#            visible=ButtonVisible
#        ) for i in range(len(anomaly[(host,group)]))]

        anomaly_data = [go.Scatter(
            x=[anomaly[anomaly.host==host].iloc[i].time,anomaly[anomaly.host==host].iloc[i].time+timedelta(hours=1)],
            y=[1,1],
            fill='tozeroy',
            fillcolor='rgba(190,127,188,0.5)',
            line=dict(width=0),
            mode= 'none',
            showlegend=False,
            visible=ButtonVisible
        ) for i in range(len(anomaly[anomaly.host==host]))]
            
        # фактические значения
        for j,metric in enumerate(metrics):
            
            if (ButtonVisible==True) & (j!=0): 
                ButtonVisible='legendonly'
                
            colorpal=random.randint(0,len(colors)-1)
            fact_data.append(go.Scatter(
                name=str(metric),
                #legendgroup=str(metric),     
                #showlegend= False,
                x=X[X.host==host].time,
                y=X[X.host==host][metric].values,
                mode='lines',
                line=dict(color=colors[colorpal][i+3]
                           ),
                visible=ButtonVisible
                )) 

        data_host[host]=list(filter(None.__ne__,[*fact_data,*anomaly_data]))

    updatemenus = list([
    dict(type="buttons",
         x = -0.07,
         buttons=list([
        dict(label='Host '+str(hostname),
          method = 'update',
          args = [
              {'visible':list(itertools.chain.from_iterable([([True]+(len(metrics)-1)*['legendonly']+(len(values)-len(metrics))*[True]) if host==hostname else len(values)*[False] for host,values in data_host.items()]
          )) },
             ])
        for i,hostname in enumerate(hosts) 
         ])
        )
 ])


    layout = dict(title=consumer_group, 
                  showlegend=True,
                  updatemenus=updatemenus,

                  xaxis=dict(
                      range=['2018-11-12','2018-11-14'],
                      rangeselector=dict(
                          buttons=list([
                              dict(count=1,
                                   label='1d',
                                   step='day',
                                   stepmode='backward'),
                              dict(count=7,
                                   label='1w',
                                   step='day',
                                   stepmode='backward'),
                              dict(count=1,
                                   label='1m',
                                   step='month',
                                   stepmode='backward'),
                              dict(step='all',
                                   stepmode='backward')
                          ]),
                      ),
                      rangeslider=dict(
                          visible = True
                      ),
                      type='date'
                  ),
                  yaxis=dict(
                      ticks='outside',
                      zeroline=False
                  ),
                 )
    #print(list(itertools.chain.from_iterable([value for key,value in data_host.items()])))
    return dict(data=list(itertools.chain.from_iterable([value for key,value in data_host.items()])), layout=layout)

   

metrics=['cpu', 'dbtime', 'iowait', 'oth_wait',
'pga', 'pxenq', 'pxqry', 'pxqtime', 'pxrel', 'read', 'reqs', 'write',
'yields', 'sys_actsess_avg', 'sys_actsess_max', 'sys_cpu', 'sys_dbtime',
'sys_iowait', 'sys_oswait', 'sys_pga', 'sys_pxqct', 'sys_pxruns',
'sys_pxsrvt', 'sys_read', 'sys_redo', 'sys_rmwait', 'sys_syspct',
'sys_ucalls', 'sys_write']

#metrics=['cpu', 'iowait', 'oth_wait']

consumer_group='szb_sandbox_group'
fig_reqs=show_forecast(df[df.consumer_group==consumer_group],metrics,consumer_group,df_predict[df_predict.consumer_group==consumer_group])
iplot(fig_reqs)